<a href="https://colab.research.google.com/github/oyyarko/nlp_projects/blob/master/IMDB_review_BERT.ipynb" target="_parent"><img src="https://colab.research.google.com/assets/colab-badge.svg" alt="Open In Colab"/></a>

In [1]:
%cd /content/drive/My Drive/Deep Learning/BERT

/content/drive/My Drive/Deep Learning/BERT


In [2]:
!curl 'https://storage.googleapis.com/kaggle-data-sets/134715/320111/bundle/archive.zip?GoogleAccessId=web-data@kaggle-161607.iam.gserviceaccount.com&Expires=1590575415&Signature=s%2BDsuxsoRCBIe5DquDcXM7l3Oo97WYVNyee9T9IcX9djioBiAB1L0gfBFLzx4aCq1K5xnlqqjcB8w3hFC%2BmoVRG6qwu5MpEJdgXJELoad%2FSk4moEWXGdKg%2FOhgUhq6pGe6CIkvZ2A5UfU14oTPfYYUX2LngWXYx7pwaVK9pgE2L%2B4gxvbxlwoUOneYBZZFTh7dLui1gl%2BDVuHqwd50PYNsaWelMcgrgM8%2Fz4DkWVLjUX3IXXJ7xbgoIpHDkCLcyr3UEW75Q%2F0NclIYidRjFufS2cLvqcX%2B%2B1mJkW%2BGcRI6H%2F58sXy3oQznfeBi8xLgEUp3obX8BETuxefkUMo5oHvA%3D%3D&response-content-disposition=attachment%3B+filename%3Dimdb-dataset-of-50k-movie-reviews.zip' -H 'User-Agent: Mozilla/5.0 (X11; Ubuntu; Linux x86_64; rv:76.0) Gecko/20100101 Firefox/76.0' -H 'Accept: text/html,application/xhtml+xml,application/xml;q=0.9,image/webp,*/*;q=0.8' -H 'Accept-Language: en-US,en;q=0.5' --compressed -o imdb_data.zip

  % Total    % Received % Xferd  Average Speed   Time    Time     Time  Current
                                 Dload  Upload   Total   Spent    Left  Speed
100 25.7M  100 25.7M    0     0  32.4M      0 --:--:-- --:--:-- --:--:-- 32.3M


In [3]:
!unzip imdb_data.zip

Archive:  imdb_data.zip
  inflating: IMDB Dataset.csv        


In [5]:
!pip install bert-for-tf2
!pip install sentencepiece

     |████████████████████████████████| 40kB 4.7MB/s 
  Created wheel for bert-for-tf2: filename=bert_for_tf2-0.14.4-cp36-none-any.whl size=30114 sha256=161b3b0cbb4936dadd181b07dd98f1201884a4a3558c5b007410c4af0db1337e
  Stored in directory: /root/.cache/pip/wheels/cf/3f/4d/79d7735015a5f523648df90d871ce8e89a7df8185f7703eeab
  Created wheel for py-params: filename=py_params-0.9.7-cp36-none-any.whl size=7302 sha256=a8d40ba6fa863b4948edce9e59c738b1940e5be4874fe7ab9de274dc9ab4fa2c
  Stored in directory: /root/.cache/pip/wheels/67/f5/19/b461849a50aefdf4bab47c4756596e82ee2118b8278e5a1980
  Created wheel for params-flow: filename=params_flow-0.8.2-cp36-none-any.whl size=19473 sha256=f471bb77bb5b64416237272b12a731c0c4399a80de99c6792c816684841a8460
  Stored in directory: /root/.cache/pip/wheels/08/c8/7f/81c86b9ff2b86e2c477e3914175be03e679e596067dc630c06
Successfully built bert-for-tf2 py-params params-flow
     |████████████████████████████████| 1.1MB 18.5MB/s 


In [0]:
%tensorflow_version 2.x
import tensorflow as tf
import tensorflow_hub as hub
from tensorflow.keras import layers
import bert
import pandas as pd

In [7]:
print(tf.__version__)

2.2.0


In [10]:
movie_reviews = pd.read_csv('IMDB Dataset.csv')
movie_reviews.head()

review sentiment
0  One of the other reviewers has mentioned that ...  positive
1  A wonderful little production. <br /><br />The...  positive
2  I thought this was a wonderful way to spend ti...  positive
3  Basically there's a family where a little boy ...  negative
4  Petter Mattei's "Love in the Time of Money" is...  positive

In [11]:
movie_reviews.shape

(50000, 2)

In [12]:
movie_reviews.isnull().values.any()

False

In [14]:
movie_reviews.info()

<class 'pandas.core.frame.DataFrame'>
RangeIndex: 50000 entries, 0 to 49999
Data columns (total 2 columns):
 #   Column     Non-Null Count  Dtype 
---  ------     --------------  ----- 
 0   review     50000 non-null  object
 1   sentiment  50000 non-null  object
dtypes: object(2)
memory usage: 781.4+ KB


In [0]:
import re
#removing all html tags
TAG_RE = re.compile(r'<[^>]+>')

def remove_tags(text):
    return TAG_RE.sub('', text)

def preprocess_text(sen):
    # Removing html tags
    sentence = remove_tags(sen)

    # Remove punctuations and numbers
    sentence = re.sub('[^a-zA-Z]', ' ', sentence)

    # Single character removal
    sentence = re.sub(r"\s+[a-zA-Z]\s+", ' ', sentence)

    # Removing multiple spaces
    sentence = re.sub(r'\s+', ' ', sentence)

    return sentence

In [0]:
reviews = []
sentences = list(movie_reviews["review"])
for sen in sentences:
    reviews.append(preprocess_text(sen))

In [22]:
reviews[:20]

['One of the other reviewers has mentioned that after watching just Oz episode you ll be hooked They are right as this is exactly what happened with me The first thing that struck me about Oz was its brutality and unflinching scenes of violence which set in right from the word GO Trust me this is not show for the faint hearted or timid This show pulls no punches with regards to drugs sex or violence Its is hardcore in the classic use of the word It is called OZ as that is the nickname given to the Oswald Maximum Security State Penitentary It focuses mainly on Emerald City an experimental section of the prison where all the cells have glass fronts and face inwards so privacy is not high on the agenda Em City is home to many Aryans Muslims gangstas Latinos Christians Italians Irish and more so scuffles death stares dodgy dealings and shady agreements are never far away would say the main appeal of the show is due to the fact that it goes where other shows wouldn dare Forget pretty pictur

In [24]:
movie_reviews.columns.values

array(['review', 'sentiment'], dtype=object)

In [26]:
movie_reviews.sentiment.unique()

array(['positive', 'negative'], dtype=object)

In [0]:
import numpy as np
y = movie_reviews['sentiment']
y = np.array(list(map(lambda x: 1 if x=='positive' else 0, y)))

In [29]:
y

array([1, 1, 1, ..., 0, 0, 0])

In [30]:
print(reviews[10])

Phil the Alien is one of those quirky films where the humour is based around the oddness of everything rather than actual punchlines At first it was very odd and pretty funny but as the movie progressed didn find the jokes or oddness funny anymore Its low budget film thats never problem in itself there were some pretty interesting characters but eventually just lost interest imagine this film would appeal to stoner who is currently partaking For something similar but better try Brother from another planet 


In [32]:
print(y[10])

0


In [0]:
BertTokenizer = bert.bert_tokenization.FullTokenizer
bert_layer = hub.KerasLayer("https://tfhub.dev/tensorflow/bert_en_uncased_L-12_H-768_A-12/1",
                            trainable=False)

vocabulary_file = bert_layer.resolved_object.vocab_file.asset_path.numpy()
to_lower_case = bert_layer.resolved_object.do_lower_case.numpy()
tokenizer = BertTokenizer(vocabulary_file, to_lower_case)

In [34]:
tokenizer.tokenize("hey there, hope you're doing good!")

['hey', 'there', ',', 'hope', 'you', "'", 're', 'doing', 'good', '!']

In [35]:
tokenizer.convert_tokens_to_ids(tokenizer.tokenize("hey there, hope you're doing good!"))

[4931, 2045, 1010, 3246, 2017, 1005, 2128, 2725, 2204, 999]

In [0]:
def tokenize_reviews(text):
    return tokenizer.convert_tokens_to_ids(tokenizer.tokenize(text))

In [0]:
tokenized_reviews = [tokenize_reviews(review) for review in reviews]

In [39]:
tokenized_reviews[:10]

[[2028,
  1997,
  1996,
  2060,
  15814,
  2038,
  3855,
  2008,
  2044,
  3666,
  2074,
  11472,
  2792,
  2017,
  2222,
  2022,
  13322,
  2027,
  2024,
  2157,
  2004,
  2023,
  2003,
  3599,
  2054,
  3047,
  2007,
  2033,
  1996,
  2034,
  2518,
  2008,
  4930,
  2033,
  2055,
  11472,
  2001,
  2049,
  24083,
  1998,
  4895,
  10258,
  2378,
  8450,
  5019,
  1997,
  4808,
  2029,
  2275,
  1999,
  2157,
  2013,
  1996,
  2773,
  2175,
  3404,
  2033,
  2023,
  2003,
  2025,
  2265,
  2005,
  1996,
  8143,
  18627,
  2030,
  5199,
  3593,
  2023,
  2265,
  8005,
  2053,
  17957,
  2007,
  12362,
  2000,
  5850,
  3348,
  2030,
  4808,
  2049,
  2003,
  13076,
  1999,
  1996,
  4438,
  2224,
  1997,
  1996,
  2773,
  2009,
  2003,
  2170,
  11472,
  2004,
  2008,
  2003,
  1996,
  8367,
  2445,
  2000,
  1996,
  17411,
  4555,
  3036,
  2110,
  7279,
  4221,
  12380,
  2854,
  2009,
  7679,
  3701,
  2006,
  14110,
  2103,
  2019,
  6388,
  2930,
  1997,
  1996,
  3827,
  2073,
  

In [0]:
reviews_with_len = [[review, y[i], len(review)] 
                    for i, review in enumerate(tokenized_reviews)]

In [0]:
import random
random.shuffle(reviews_with_len)

In [42]:
reviews_with_len

[[[2383,
   2657,
   3243,
   3893,
   4391,
   1998,
   2383,
   2464,
   1996,
   9117,
   2018,
   2000,
   2156,
   2023,
   3185,
   2007,
   2520,
   20914,
   6446,
   22789,
   2745,
   6892,
   2121,
   1998,
   3520,
   25235,
   2556,
   2009,
   2018,
   2000,
   2022,
   2204,
   1998,
   2009,
   5359,
   3452,
   1996,
   3185,
   2003,
   2025,
   8579,
   2017,
   2039,
   6057,
   2021,
   2045,
   2003,
   2028,
   3496,
   2008,
   2428,
   4832,
   2041,
   1998,
   2003,
   1999,
   2026,
   2159,
   4438,
   27594,
   2121,
   2012,
   1996,
   2203,
   2073,
   2027,
   3338,
   2083,
   1996,
   2813,
   2000,
   2131,
   2000,
   1996,
   3647,
   1998,
   2057,
   2156,
   25235,
   1998,
   2899,
   6237,
   2012,
   6892,
   2121,
   2003,
   2074,
   10392,
   2023,
   2003,
   2074,
   2004,
   2204,
   2004,
   1996,
   3496,
   1999,
   1996,
   2502,
   3393,
   18912,
   5488,
   2073,
   1996,
   12043,
   2003,
   2478,
   3242,
   2000,
   19820,
 

In [0]:
reviews_with_len.sort(key= lambda x: x[2])

In [0]:
sorted_reviews_labels = [(review_lab[0], review_lab[1]) for review_lab in reviews_with_len]

In [0]:
#now convert it into Tensorflow- 2.0 competant
processed_dataset = tf.data.Dataset.from_generator(
    lambda: sorted_reviews_labels, output_types=(tf.int32, tf.int32)
)

In [0]:
BATCH_SIZE = 32
batched_dataset = processed_dataset.padded_batch(
    BATCH_SIZE, padded_shapes=((None, ), ())
)

In [47]:
next(iter(batched_dataset))

(<tf.Tensor: shape=(32, 21), dtype=int32, numpy=
 array([[ 3078,  5436,  3078,  3257,  3532,  7613,     0,     0,     0,
             0,     0,     0,     0,     0,     0,     0,     0,     0,
             0,     0,     0],
        [ 3191,  1996,  2338,  5293,  1996,  3185,     0,     0,     0,
             0,     0,     0,     0,     0,     0,     0,     0,     0,
             0,     0,     0],
        [ 2054,  5896,  2054,  2466,  2054,  6752,     0,     0,     0,
             0,     0,     0,     0,     0,     0,     0,     0,     0,
             0,     0,     0],
        [ 2062, 23873,  3993,  2062, 11259,  2172,  2172,  2062, 14888,
             0,     0,     0,     0,     0,     0,     0,     0,     0,
             0,     0,     0],
        [ 2023,  3185,  2003,  6659,  2021,  2009,  2038,  2070,  2204,
          3896,     0,     0,     0,     0,     0,     0,     0,     0,
             0,     0,     0],
        [ 1045,  2876,  9278,  2023,  2028,  2130,  2006,  7922, 12635,
    

In [0]:
import math

TOTAL_BATCHES = math.ceil(len(sorted_reviews_labels) / BATCH_SIZE)
TEST_BATCHES = TOTAL_BATCHES // 10 #10% for testing
batched_dataset.shuffle(TOTAL_BATCHES)
test_data = batched_dataset.take(TEST_BATCHES)
train_data = batched_dataset.skip(TEST_BATCHES)

In [0]:
class TEXT_MODEL(tf.keras.Model):
    def __init__(self,
                 vocabulary_size,
                 embedding_dimensions=128,
                 cnn_filters=50,
                 dnn_units=512,
                 model_output_classes=2,
                 dropout_rate=0.1,
                 training=False,
                 name="text_model"):
        super(TEXT_MODEL, self).__init__(name=name)
        self.embedding = layers.Embedding(vocabulary_size, 
                                          embedding_dimensions)
        self.cnn_layer1 = layers.Conv1D(filters=cnn_filters,
                                       kernel_size=2,
                                       padding='valid',
                                       activation='relu')
        self.cnn_layer2 = layers.Conv1D(filters=cnn_filters,
                                       kernel_size=3,
                                       padding='valid',
                                       activation='relu')
        self.cnn_layer3 = layers.Conv1D(filters=cnn_filters,
                                       kernel_size=4,
                                       padding='valid',
                                       activation='relu')
        self.pool = layers.GlobalMaxPool1D()

        self.dense_1 = layers.Dense(units=dnn_units, 
                                    activation='relu')
        
        self.dropout = layers.Dropout(rate=dropout_rate)
        if model_output_classes == 2:
            self.last_dense = layers.Dense(units=1,
                                           activation='sigmoid')
        else:
            self.last_dense = layers.Dense(units=model_output_classes,
                                           activation='softmax')
            
    def call(self, inputs, training):
        l = self.embedding(inputs)
        l_1 = self.cnn_layer1(l)
        l_1 = self.pool(l_1)
        l_2 = self.cnn_layer1(l)
        l_2 = self.pool(l_2)
        l_3 = self.cnn_layer1(l)
        l_3 = self.pool(l_3)

        concatenated = tf.concat([l_1, l_2, l_3], axis=-1)
        concatenated = self.dense_1(concatenated)
        concatenated = self.dropout(concatenated, training)
        model_output = self.last_dense(concatenated)

        return model_output

In [0]:
VOCAB_LENGTH = len(tokenizer.vocab)
EMB_DIM = 200
CNN_FILTERS = 100
DNN_UNITS = 256
OUTPUT_CLASSES = 2
DROPOUT_RATE = 0.2
NB_EPOCHS = 5

In [0]:
text_model = TEXT_MODEL(vocabulary_size=VOCAB_LENGTH,
                        embedding_dimensions=EMB_DIM,
                        cnn_filters=CNN_FILTERS,
                        dnn_units=DNN_UNITS,
                        model_output_classes=OUTPUT_CLASSES,
                        dropout_rate=DROPOUT_RATE)

In [0]:
if OUTPUT_CLASSES == 2:
    text_model.compile(loss='binary_crossentropy',
                       optimizer="adam",
                       metrics=['accuracy'])
else:
    text_model.compile(loss='categorical_crossentropy',
                       optimizer="adam",
                       metrics=['accuracy'])

In [59]:
text_model.fit(train_data, epochs=NB_EPOCHS)

Epoch 1/5
1407/1407 [==============================] - 116s 83ms/step - loss: 0.3179 - accuracy: 0.8588
Epoch 2/5
1407/1407 [==============================] - 91s 65ms/step - loss: 0.1681 - accuracy: 0.9366
Epoch 3/5
1407/1407 [==============================] - 93s 66ms/step - loss: 0.0924 - accuracy: 0.9676
Epoch 4/5
1407/1407 [==============================] - 92s 65ms/step - loss: 0.0621 - accuracy: 0.9772
Epoch 5/5
1407/1407 [==============================] - 92s 65ms/step - loss: 0.0352 - accuracy: 0.9866


In [61]:
results = text_model.evaluate(test_data)
print(results)

156/156 [==============================] - 5s 29ms/step - loss: 0.4238 - accuracy: 0.8884
[0.42384347319602966, 0.8884214758872986]


In [0]:
def get_prediction(sen):
    tokens = tokenize_reviews(sen)
    inputs = tf.expand_dims(tokens, 0)

    output = text_model(inputs, training=False)
    sentiment = math.floor(output*2)
    if sentiment == 0:
        print("Ouput of the model: {}\nPredicted sentiment: negative.".format(
            output))
    elif sentiment == 1:
        print("Ouput of the model: {}\nPredicted sentiment: positive.".format(
            output))

In [68]:
get_prediction("ohh sure, hope you get brain")

Ouput of the model: [[0.08016083]]
Predicted sentiment: negative.
